# This Notebook:
“A Maximum Likelihood Bunching Estimator of the Elasticity of Taxable Income” written by Thomas Aronsson, Katharina Jenderny and Gauthier Lanot, accepted for publication in the Journal of Applied Econometrics, MS-13011.

This notebook applies the Chetty approach to the estimation of the ETI using Swedish evidence. 

This file deals with "ETI_hist_FInk_taxable1000_bin100_2019.dta".

We have first a bunch of declaration (functions etc...), then a presentation of the data, and then some calculations. The calculations are slightly more extensive than those presented in the text of the paper. This may convince the reader that we have carried out due diligence...

In [ ]:
#Parallelism().set(nproc=6)
#print(Parallelism())

In [ ]:
import numpy  as np
import pandas as pd
import os

In [ ]:
tt=os.getcwd()
show(tt)

In [ ]:
#hessian, for var cov+ checking optimum...
# hh0b=matrix(RDF,hes(lik0,q00b))
# hh0b.eigenvalues()
# hh0ib = hh0b.inverse()
# sqrtN =sqrt(sum(n[1] for n in nobs))
# results log-likelihood estimates...
# res_lik_print0(q00b,hh0ib,sqrtN,sum(n[1] for n in nobs),"Likelihood Estimates, Homoscedastic Model")


# Tax Info

In [ ]:
# this is for UMea...what is the swedish average...?
taxinfo = [ [2001,0.677,0.477,252000],
         [2002,0.677,0.477,273800],
         [2003,0.677,0.477,284300],
         [2004,0.677,0.477,291800],
         [2005,0.669,0.469,298600],
         [2006,0.669,0.469,306000],
         [2007,0.669,0.469,316700],        
         [2008,0.669,0.469,328800],
         [2009,0.669,0.469,367600],
         [2010,0.669,0.469,372100],
         [2011,0.669,0.469,383000],
         [2012,0.669,0.469,401100],
         [2013,0.669,0.469,413200],
         [2014,0.664,0.464,420800],
         [2015,0.664,0.464,430200],
         [2016,0.6635,0.4635,430200],
         [2017,0.6585,0.46585,438900],
         [2018,0.6585,0.46585,455300],
         [2019,0.6585,0.46585,490700]
       ]

In [ ]:
# so how do we select a symmetric range around the kink...?
# we check the distance from the kink to the min or the max, 
# and select only if the difference from the kink 
# is less that the minimum between those 2 differences... simple...
year = 2019
Info_in_year = flatten([ nn for nn in taxinfo if nn[0]==year])
Kink = Info_in_year[3]/1000.
lnk=ln(Kink).n()

In [ ]:
os.chdir(tt)
tt2=os.getcwd()
show(tt2)

# Data:
Here comes the data. 

In [ ]:
import numpy  as np
import pandas as pd
import os

In [ ]:
#newd="D://Umeå universitet//ETI - General//JAE Revisions//scb data//hist_data"
#newd = "/Users/gauthierlanot/Library/CloudStorage/OneDrive-SharedLibraries-Umeåuniversitet/ETI - General/JAE Revisions/scb data/"
#newd = "//Users/gauthierlanot/Downloads/"
#ETI - General\\JAE Revisions\\scb data"
newd = "D:\ETIprojectfiles\JAE revisions"
show(newd)

In [ ]:
# loading data from stata file
os.chdir(newd)
filename = "ETI_hist_FInk_taxable1000_bin100_2019.dta"

In [ ]:
dd0 = pd.read_stata(filename)

In [ ]:
dd = dd0.to_numpy()

In [ ]:
dd = [(nn[0],nn[1],nn[2],nn[3]/1000.,nn[4],nn[5],nn[6]/1000.) for nn in dd]

In [ ]:
# ...and here we find that the data is not centered on the kink! 
# typical last minute job! no attention to details!
#df0

In [ ]:
dd[0:10]

In [ ]:
# so how do we select a symmetric range around the kink...?
# we check the distance from the kink to the min or the max, 
# and select only if the difference from the kink 
# is less that the minimum between those 2 differences... simple...
year = 2019
Info_in_year = flatten([ nn for nn in taxinfo if nn[0]==year])
Kink = Info_in_year[3]/1000.
lnk=ln(Kink).n()

In [ ]:
Info_in_year

In [ ]:
Kink

In [ ]:
dd[0]

In [ ]:
#distmin2k = df0.kink[[0]].array[0]-df0.wh[[0]].array[0]
#distk2max = df0.wh[[len(df0)-1]].array[0]-df0.kink[[0]].array[0]
#topdistfromk = min(distmin2k,distk2max)+0.001
#distmin2k,distk2max,topdistfromk
distmin2k = dd[0][6]-dd[0][3]
distk2max = dd[-1][3]-dd[-1][6]
topdistfromk = min(distmin2k,distk2max)+0.001
distmin2k,distk2max,topdistfromk

In [ ]:
df = [nn for nn in dd if abs(nn[3]-Kink)<=topdistfromk ]
df_yy_cnt = [ (dd[3],dd[1]) for dd in df]

In [ ]:
df_yy_cnt[0:10]

In [ ]:
list_plot(df_yy_cnt)

In [ ]:
# transform data into array...
#df1 = df0.to_numpy()
#and select to make range centered on kink
#df = [nn for nn in df1 if abs(nn[3]-Kink)<=topdistfromk ]
df = [nn for nn in dd if abs(nn[3]-Kink)<=topdistfromk ]

In [ ]:
df[0:10],lnk,Kink

In [ ]:
Nobs = int(sum([nn[1] for nn in df]))
show(Nobs)
dens = [(nn[3],nn[1]/Nobs) for nn in df]
dens = np.array(dens)
show(len(dens))

#densa = [(nn[3],nn[1]/Nobs/0.1) for nn in df if not(((ln(nn[3])+0.1/252.)>=lnk) and (ln(nn[3])<=lnk) )]

densa = [(nn[3],nn[1]/Nobs/0.1) for nn in df if nn[3]<(Kink-0.0999)]+ \
        [(nn[3],nn[1]/Nobs) for nn in df if (nn[3]>=(Kink-0.0999)) and (nn[3])<=Kink]+\
        [(nn[3],nn[1]/Nobs/0.1) for nn in df if nn[3]>Kink]
        
densb = [(nn[3],nn[1]/Nobs/0.1) for nn in df] 


In [ ]:
sum([nn[1] for nn in densa if nn[0]<(Kink-0.0999)])*0.1+\
sum([nn[1] for nn in densa if nn[0]>(Kink)])*0.1+\
sum([nn[1] for nn in densa if (nn[0]>=(Kink-0.0999)) and (nn[0])<=Kink])

In [ ]:
[nn for nn in densa if (nn[0]>=(Kink-0.1)) and (nn[0])<=Kink]

In [ ]:
type(Nobs), sum([nn[1] for nn in densb]), sum([nn[1] for nn in densa])

In [ ]:
[(nn[3],nn[1]/Nobs) for nn in df if (nn[3]>(Kink-0.099)) and (nn[3]-Kink)<=0]

In [ ]:
[ n for n in dens if (((ln(n[0])+0.1/Kink)>=lnk) and (ln(n[0])<=lnk)) ]

In [ ]:
[(nn[3],(nn[1]/Nobs),nn[1]/Nobs/0.1) for nn in df if nn[3]>(Kink-2) and nn[3]<(Kink+2)]

In [ ]:
sum([n[1] for n in dens]),sum([n[1] for n in densa])

In [ ]:
list_plot(dens[int(len(dens)/2)-5:int(len(dens)/2)+5])+list_plot(densa[int(len(dens)/2)-5:int(len(dens)/2)+5],color='red',alpha=0.3)


In [ ]:
list_plot(densa)

In [ ]:
#sum(dens[n][1] for n in range(0,len(dens)) if n!= KinkPos)+dens[KinkPos][1]

In [ ]:
os.chdir(tt)
tt2=os.getcwd()
show(tt2)

## Transformations:
The data is transformed in several ways:
+ dens: contains the data as density everywhere but at the kink where it is a probability, used for least squares fitting, model with perfect bunching;
+ densa: containes the data as proportion of the sample, used for maximum likelihood, model with perfect bunching;
+ densb: contains the data as density everywhere, used for least squares fitting, model with imperfect bunching.


In [ ]:
totnobs = Nobs

KinkPos = int((len(df)-1)/2)

print(sum( n[1] for n in dens))

#best normal fit...
# measure mean and variance
print("level")
m  = sum(n[1]*n[0]   for n in dens)
m2 = sum(n[1]*n[0]^2 for n in dens)
v2 = m2-m^2
print(['mean',m],['std dev',sqrt(m2-m^2)])

print("logs")
lm = sum( n[1]*log(n[0]) for n in dens)
lm2 = sum(n[1]*log(n[0])^2 for n in dens)
lv2 = lm2-lm^2
print(['mean',lm],['std dev',sqrt(lm2-lm^2)])
# -1. to deal with the data to the left of the lower bound...
# to copy in the spyx file...until I find how to transfer data on the fly!

lnebu = ln(min(n[0] for n in dens)-.1)
lnebo = ln(max(n[0] for n in dens))



sum(dens[n][1] for n in range(0,len(dens)) if n!= KinkPos)+dens[KinkPos][1],\
sum(dens[n][1] for n in range(0,len(dens)) )

In [ ]:
lnebu,lnebo

In [ ]:
KinkPos,dens[KinkPos]

In [ ]:
# allows us to check the data!
#list_plot(dens,ymin=0)+ list_plot(densa,color='gold')

In [ ]:
Info_in_year

In [ ]:
#list(zip(dens,densa))
Info_in_year[1]

## Tax parameters:

In [ ]:
pl1,pl2,ps,ps1,ps2,pr12,lw,delta = var('pl1,pl2,ps,ps1,ps2,pr12,lw,delta')
delta = (0.1*.99999)
#/Kink

# this is complicated since their application aggregates many years...here I take the rates for 2004...
lnt1c = ln(Info_in_year[1])
lnt2c = ln(Info_in_year[2])
lt1cplt2c = lnt1c^2 + lnt2c^2
lt1cmlt2c = lnt1c^2 - lnt2c^2

In [ ]:
delta,delta/(lnt1c-lnt2c)

In [ ]:
delta,lnk,dens[KinkPos][0],Kink

In [ ]:
#len(df_yy_cnt),Kink
#ck['IG'][0:10],ck['FREQ'][0:10]
#show(list(zip(ck['IG'].list(),ck['FREQ'].list())))

## Chetty Polynomial Bunching Estimation, all data
8 different size of the excluded range...
<br>
+/- 5
<br>
+/- 10
<br>
+/- 15
<br>
+/- 20
<br>
+/- 25
<br>
+/- 50
<br>
+/- 75
<br>
+/- 100
<br>
STEP_BIN=0.1

In [ ]:
load("chetty_bunch.py")

In [ ]:
#bin size (this is more important than you would think!)
STEP_BIN = 0.1

In [ ]:
st1 = bin_to_bin(df_yy_cnt,Kink,STEP_BIN,(len(df_yy_cnt)-1)/2)
chetty_tab = []
for exzone in [5,10,15,20,25,50,75,100]:   
    # IG, FREQ, list_cnt
    st2 = design_bunch(st1['IG'],st1['FREQ'],Kink,-exzone,exzone,7)
    st3 = chetty_poly_bunch_court(st1['IG'],st1['FREQ'],st2['X'],st2['X_nodum'],st2['XXinvX'] ,st2['get_beta_poly'],st2['get_beta_dummy'],st2['ndum'],st2['people_nearbunch'])
    eresid = [st3['resid'][i][0] for i in range(0,len(st3['y_hat_org'].list())) if abs(st1['IG'][i])>50]
    res = lp(st1,st2,st3,eresid,exzone)
    chetty_central_a = st3['b']/(lnt1c-lnt2c)/Kink*STEP_BIN
    to_plot = [a[1]/(lnt1c-lnt2c)/Kink*STEP_BIN for a in res]
    to_plot.sort()
    ltp = len(to_plot)
    chetty_tab.append([chetty_central_a,mean(to_plot),to_plot[round(ltp*.05)],to_plot[round(ltp*.25)],to_plot[round(ltp*.75)],to_plot[round(ltp*.95)],std(to_plot)])
    

In [ ]:
# make a presentable table!
table([map_threaded(lambda x: round(x,3), nn) for nn in list(chetty_tab)],\
      header_row=["Estimate","Bstp-mean","Bstp-5%","Bstp-25%","Bstp-75%","Bstp-95%","Bstp-std dev"],\
      header_column=["","Chetty, 5","Chetty, 10","Chetty, 15","Chetty, 20","Chetty, 25","Chetty, 50","Chetty, 75","Chetty, 100"])

In [ ]:
latex(table([map_threaded(lambda x: round(x,3), nn) for nn in list(chetty_tab)],\
      header_row=["Estimate","Bstp-mean","Bstp-5%","Bstp-25%","Bstp-75%","Bstp-95%","Bstp-std dev"],\
      header_column=["","Chetty, 5","Chetty, 10","Chetty, 15","Chetty, 20","Chetty, 25","Chetty, 50","Chetty, 75","Chetty, 100"]))

In [ ]:
# this would produce some graph...
#chetty_central_a = st3['b']/(lnt1c-lnt2c)/Kink*STEP_BIN
#to_plot = [a[1]/(lnt1c-lnt2c)/Kink*0.1 for a in res]
#mean_to_plot = mean(to_plot)
#sdv_to_plot = sqrt(variance(to_plot,bias=True))
#show([mean_to_plot,sdv_to_plot])
#P = plot(pdfn((x-mean_to_plot)/sdv_to_plot)/sdv_to_plot, (x, mean_to_plot-5.*sdv_to_plot, mean_to_plot+5.*sdv_to_plot), color='magenta', linestyle='--',thickness=1)
#L_ch = line([(chetty_central_a,0),(chetty_central_a,1.2*pdfn(0.)/sdv_to_plot)],color='gold')
#histogram(to_plot,bins=131,density=True)+P+L_ch

## Chetty Polynomial Bunching Estimation, 450.7-530.7
8 different size of the excluded range...
<br>
+/- 5
<br>
+/- 10
<br>
+/- 15
<br>
+/- 20
<br>
+/- 25
<br>
+/- 50
<br>
+/- 75
<br>
+/- 100
<br>
STEP_BIN=0.1

In [ ]:
load("chetty_bunch.py")

In [ ]:
#bin size (this is more important than you would think!)
STEP_BIN = 0.1

In [ ]:
#data selection
topdistfromk = 40+0.001


df = [nn for nn in dd if abs(nn[3]-Kink)<=topdistfromk ]
df_yy_cnt = [ (dd[3],dd[1]) for dd in df]
Nobs = int(sum([nn[1] for nn in df]))
show(Nobs)
show(len(df_yy_cnt))



In [ ]:
st1 = bin_to_bin(df_yy_cnt,Kink,STEP_BIN,(len(df_yy_cnt)-1)/2)
chetty_tab = []
for exzone in [5,10,15,20,25,50,75,100]:   
    # IG, FREQ, list_cnt
    st2 = design_bunch(st1['IG'],st1['FREQ'],Kink,-exzone,exzone,7)
    st3 = chetty_poly_bunch_court(st1['IG'],st1['FREQ'],st2['X'],st2['X_nodum'],st2['XXinvX'] ,st2['get_beta_poly'],st2['get_beta_dummy'],st2['ndum'],st2['people_nearbunch'])
    eresid = [st3['resid'][i][0] for i in range(0,len(st3['y_hat_org'].list())) if abs(st1['IG'][i])>50]
    res = lp(st1,st2,st3,eresid,exzone)
    chetty_central_a = st3['b']/(lnt1c-lnt2c)/Kink*STEP_BIN
    to_plot = [a[1]/(lnt1c-lnt2c)/Kink*STEP_BIN for a in res]
    to_plot.sort()
    ltp = len(to_plot)
    chetty_tab.append([chetty_central_a,mean(to_plot),to_plot[round(ltp*.05)],to_plot[round(ltp*.25)],to_plot[round(ltp*.75)],to_plot[round(ltp*.95)],std(to_plot)])
    

In [ ]:
# make a presentable table!
table([map_threaded(lambda x: round(x,3), nn) for nn in list(chetty_tab)],\
      header_row=["Estimate","Bstp-mean","Bstp-5%","Bstp-25%","Bstp-75%","Bstp-95%","Bstp-std dev"],\
      header_column=["","Chetty, 5","Chetty, 10","Chetty, 15","Chetty, 20","Chetty, 25","Chetty, 50","Chetty, 75","Chetty, 100"])

In [ ]:
latex(table([map_threaded(lambda x: round(x,3), nn) for nn in list(chetty_tab)],\
      header_row=["Estimate","Bstp-mean","Bstp-5%","Bstp-25%","Bstp-75%","Bstp-95%","Bstp-std dev"],\
      header_column=["","Chetty, 5","Chetty, 10","Chetty, 15","Chetty, 20","Chetty, 25","Chetty, 50","Chetty, 75","Chetty, 100"]))

In [ ]:
# this would produce some graph...
#chetty_central_a = st3['b']/(lnt1c-lnt2c)/Kink*STEP_BIN
#to_plot = [a[1]/(lnt1c-lnt2c)/Kink*0.1 for a in res]
#mean_to_plot = mean(to_plot)
#sdv_to_plot = sqrt(variance(to_plot,bias=True))
#show([mean_to_plot,sdv_to_plot])
#P = plot(pdfn((x-mean_to_plot)/sdv_to_plot)/sdv_to_plot, (x, mean_to_plot-5.*sdv_to_plot, mean_to_plot+5.*sdv_to_plot), color='magenta', linestyle='--',thickness=1)
#L_ch = line([(chetty_central_a,0),(chetty_central_a,1.2*pdfn(0.)/sdv_to_plot)],color='gold')
#histogram(to_plot,bins=131,density=True)+P+L_ch

## Chetty Polynomial Bunching Estimation, 475.7-505.7
8 different size of the excluded range...
<br>
+/- 5
<br>
+/- 10
<br>
+/- 15
<br>
+/- 20
<br>
+/- 25
<br>
+/- 50
<br>
+/- 75
<br>
+/- 100
<br>
STEP_BIN=0.1

In [ ]:
load("chetty_bunch.py")

In [ ]:
#bin size (this is more important than you would think!)
STEP_BIN = 0.1

In [ ]:
#data selection
topdistfromk = 15+0.001
df = [nn for nn in dd if abs(nn[3]-Kink)<=topdistfromk ]
df_yy_cnt = [ (dd[3],dd[1]) for dd in df]
Nobs = int(sum([nn[1] for nn in df]))
show(Nobs)
show(len(df_yy_cnt))


In [ ]:
st1 = bin_to_bin(df_yy_cnt,Kink,STEP_BIN,(len(df_yy_cnt)-1)/2)
chetty_tab = []
for exzone in [5,10,15,20,25,50,75,100]:   
    # IG, FREQ, list_cnt
    st2 = design_bunch(st1['IG'],st1['FREQ'],Kink,-exzone,exzone,7)
    st3 = chetty_poly_bunch_court(st1['IG'],st1['FREQ'],st2['X'],st2['X_nodum'],st2['XXinvX'] ,st2['get_beta_poly'],st2['get_beta_dummy'],st2['ndum'],st2['people_nearbunch'])
    eresid = [st3['resid'][i][0] for i in range(0,len(st3['y_hat_org'].list())) if abs(st1['IG'][i])>50]
    res = lp(st1,st2,st3,eresid,exzone)
    chetty_central_a = st3['b']/(lnt1c-lnt2c)/Kink*STEP_BIN
    to_plot = [a[1]/(lnt1c-lnt2c)/Kink*STEP_BIN for a in res]
    to_plot.sort()
    ltp = len(to_plot)
    chetty_tab.append([chetty_central_a,mean(to_plot),to_plot[round(ltp*.05)],to_plot[round(ltp*.25)],to_plot[round(ltp*.75)],to_plot[round(ltp*.95)],std(to_plot)])
    

In [ ]:
# make a presentable table!
table([map_threaded(lambda x: round(x,3), nn) for nn in list(chetty_tab)],\
      header_row=["Estimate","Bstp-mean","Bstp-5%","Bstp-25%","Bstp-75%","Bstp-95%","Bstp-std dev"],\
      header_column=["","Chetty, 5","Chetty, 10","Chetty, 15","Chetty, 20","Chetty, 25","Chetty, 50","Chetty, 75","Chetty, 100"])

In [ ]:
latex(table([map_threaded(lambda x: round(x,3), nn) for nn in list(chetty_tab)],\
      header_row=["Estimate","Bstp-mean","Bstp-5%","Bstp-25%","Bstp-75%","Bstp-95%","Bstp-std dev"],\
      header_column=["","Chetty, 5","Chetty, 10","Chetty, 15","Chetty, 20","Chetty, 25","Chetty, 50","Chetty, 75","Chetty, 100"]))

In [ ]:
# this would produce some graph...
#chetty_central_a = st3['b']/(lnt1c-lnt2c)/Kink*STEP_BIN
#to_plot = [a[1]/(lnt1c-lnt2c)/Kink*0.1 for a in res]
#mean_to_plot = mean(to_plot)
#sdv_to_plot = sqrt(variance(to_plot,bias=True))
#show([mean_to_plot,sdv_to_plot])
#P = plot(pdfn((x-mean_to_plot)/sdv_to_plot)/sdv_to_plot, (x, mean_to_plot-5.*sdv_to_plot, mean_to_plot+5.*sdv_to_plot), color='magenta', linestyle='--',thickness=1)
#L_ch = line([(chetty_central_a,0),(chetty_central_a,1.2*pdfn(0.)/sdv_to_plot)],color='gold')
#histogram(to_plot,bins=131,density=True)+P+L_ch